In [1]:
import pandas as pd
import numpy as np

In [2]:
drinks_df =pd.read_csv('Drink_Sales.csv')

In [3]:
drinks_df.head()

respondent_id  age gender   zone            occupation income_levels  \
0        R00001   30      M  Urban  Working Professional          <10L   
1        R00002   46      F  Metro  Working Professional         > 35L   
2        R00003   41      F  Rural  Working Professional         > 35L   
3        R00004   33      F  Urban  Working Professional     16L - 25L   
4        R00005   23      M  Metro               Student  Not Reported   

  consume_frequency(weekly) current_brand preferable_consumption_size  \
0                 3-4 times      Newcomer             Medium (500 ml)   
1                 5-7 times   Established             Medium (500 ml)   
2                 3-4 times      Newcomer             Medium (500 ml)   
3                 5-7 times      Newcomer             Medium (500 ml)   
4                 3-4 times   Established             Medium (500 ml)   

  awareness_of_other_brands  ... flavor_preference purchase_channel  \
0                    0 to 1  ...       Traditional           Online   
1                    2 to 4  ...            Exotic     Retail Store   
2                    2 to 4  ...       Traditional     Retail Store   
3                    0 to 1  ...            Exotic           Online   
4                    0 to 1  ...       Traditional           Online   

  packaging_preference                       health_concerns  \
0               Simple  Medium (Moderately health-conscious)   
1              Premium  Medium (Moderately health-conscious)   
2              Premium  Medium (Moderately health-conscious)   
3         Eco-Friendly              Low (Not very concerned)   
4              Premium  Medium (Moderately health-conscious)   

  typical_consumption_situations price_range age_group cf_ab_score  zas_score  \
0       Active (eg. Sports, gym)     100-150     26-35        0.67          3   
1           Social (eg. Parties)     200-250     46-55        0.60         20   
2       Active (eg. Sports, gym)     200-250     36-45        0.50          5   
3       Active (eg. Sports, gym)     150-200     26-35        0.75          9   
4       Active (eg. Sports, gym)      50-100     18-25        0.67          0   

   bsi  
0    1  
1    0  
2    0  
3    0  
4    0  

[5 rows x 21 columns]

In [4]:
drinks_df = drinks_df.drop(columns = 'respondent_id',axis = 1)

In [5]:
X = drinks_df.drop('price_range',axis=1)
y = drinks_df['price_range']

In [6]:
from sklearn.model_selection import train_test_split
import warnings

# Suppress all warnings
warnings.filterwarnings("ignore")
X_train,X_test,y_train,y_test = train_test_split(X,y,test_size = 0.25,random_state = 42)

In [7]:
from sklearn.preprocessing import OrdinalEncoder

# Define the specific order for each ordinal column
ordinal_categories = [
    ['18-25', '26-35', '36-45', '46-55', '56-70', '70+'],  # age_group
    ['0-2 times', '3-4 times', '5-7 times'],  # consume_frequency(weekly)
    ['Small (250 ml)', 'Medium (500 ml)', 'Large (1 L)'],  # preferable_consumption_size
    ['Low (Not very concerned)', 'Medium (Moderately health-conscious)', 'High (Very health-conscious)']  # health_concerns
]

# List of your ordinal column names in the same order
ordinal_cols = [
    'age_group',
    'consume_frequency(weekly)',
    'preferable_consumption_size',
    'health_concerns'
]

# Initialize the encoder
ordinal_encoder = OrdinalEncoder(categories=ordinal_categories)

# Apply the encoding
X_train[ordinal_cols] = ordinal_encoder.fit_transform(X_train[ordinal_cols])
X_test[ordinal_cols] = ordinal_encoder.transform(X_test[ordinal_cols])

In [8]:
income_order = [['Not Reported', '<10L', '10L - 15L', '16L - 25L', '26L - 35L', '> 35L']]

# Create encoder for just income_levels
income_encoder = OrdinalEncoder(categories=income_order)

# Apply encoding
X_train[['income_levels']] = income_encoder.fit_transform(X_train[['income_levels']])
X_test[['income_levels']] = income_encoder.transform(X_test[['income_levels']])

In [9]:
nominal_cols = [
    'gender',
    'zone',
    'occupation',
    'current_brand',
    'awareness_of_other_brands',
    'reasons_for_choosing_brands',
    'flavor_preference',
    'purchase_channel',
    'packaging_preference',
    'typical_consumption_situations'
]

In [10]:
X_train = pd.get_dummies(X_train,columns = nominal_cols,drop_first = True)

In [11]:
X_test = pd.get_dummies(X_test,columns = nominal_cols,drop_first = True)

In [12]:
from sklearn.preprocessing import LabelEncoder

# Initialize the encoder
le = LabelEncoder()

# Fit and transform the target
y_train_encoded = le.fit_transform(y_train)
y_train_encoded_series = pd.Series(y_train_encoded, name='target_encoded')

In [13]:
y_test_encoded = le.transform(y_test)
y_test_encoded_series = pd.Series(y_test_encoded,name = 'target_encoded')

In [14]:
y_test_encoded_series
y_test = pd.DataFrame({
    'price_range' : y_test_encoded_series
})

In [15]:
y_train = pd.DataFrame({
    'price_range' : y_train_encoded_series
})

In [16]:
# import optuna
# import numpy as np
# from sklearn.datasets import load_breast_cancer
# from sklearn.model_selection import cross_val_score, StratifiedKFold, train_test_split
# from sklearn.preprocessing import StandardScaler
# from sklearn.pipeline import make_pipeline
# from sklearn.naive_bayes import GaussianNB
# from sklearn.linear_model import LogisticRegression
# from sklearn.svm import SVC
# from sklearn.ensemble import RandomForestClassifier
# from xgboost import XGBClassifier
# from sklearn.metrics import classification_report

# # ✅ Load dataset
# X, y = load_breast_cancer(return_X_y=True)
# cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

# # ----------------------------
# # ✅ Define Objective Functions
# # ----------------------------

# def objective_gnb(trial):
#     var_smoothing = trial.suggest_float('var_smoothing', 1e-11, 1e-7, log=True)
#     model = make_pipeline(
#         StandardScaler(),
#         GaussianNB(var_smoothing=var_smoothing)
#     )
#     return cross_val_score(model, X, y, cv=cv, scoring='accuracy').mean()

# def objective_logreg(trial):
#     c = trial.suggest_float("C", 1e-4, 10.0, log=True)
#     penalty = trial.suggest_categorical("penalty", ["l2"])
#     solver = "lbfgs"
#     model = make_pipeline(
#         StandardScaler(),
#         LogisticRegression(C=c, penalty=penalty, solver=solver, max_iter=1000)
#     )
#     return cross_val_score(model, X, y, cv=cv, scoring='accuracy').mean()

# def objective_svc(trial):
#     c = trial.suggest_float("C", 1e-3, 10.0, log=True)
#     gamma = trial.suggest_float("gamma", 1e-4, 1.0, log=True)
#     kernel = trial.suggest_categorical("kernel", ["rbf", "linear"])
#     model = make_pipeline(
#         StandardScaler(),
#         SVC(C=c, gamma=gamma, kernel=kernel)
#     )
#     return cross_val_score(model, X, y, cv=cv, scoring='accuracy').mean()

# def objective_rf(trial):
#     n_estimators = trial.suggest_int("n_estimators", 50, 300)
#     max_depth = trial.suggest_int("max_depth", 3, 20)
#     min_samples_split = trial.suggest_int("min_samples_split", 2, 10)
#     model = RandomForestClassifier(
#         n_estimators=n_estimators,
#         max_depth=max_depth,
#         min_samples_split=min_samples_split,
#         random_state=42
#     )
#     return cross_val_score(model, X, y, cv=cv, scoring='accuracy').mean()

# def objective_xgb(trial):
#     param = {
#         'n_estimators': trial.suggest_int('n_estimators', 50, 300),
#         'max_depth': trial.suggest_int('max_depth', 3, 10),
#         'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3, log=True),
#         'subsample': trial.suggest_float('subsample', 0.5, 1.0),
#         'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
#         'gamma': trial.suggest_float('gamma', 0, 5),
#         'use_label_encoder': False,
#         'eval_metric': 'logloss',
#         'random_state': 42
#     }
#     model = XGBClassifier(**param)
#     return cross_val_score(model, X, y, cv=cv, scoring='accuracy').mean()

# # ---------------------------------
# # ✅ Function to Run Optuna Study
# # ---------------------------------
# def run_study(objective_fn, model_name):
#     print(f"\n🔍 Optimizing {model_name}...")
#     study = optuna.create_study(direction='maximize')
#     study.optimize(objective_fn, n_trials=30, timeout=300)
#     print(f"✅ Best Accuracy for {model_name}: {study.best_value:.4f}")
#     print(f"🧠 Best Params: {study.best_params}")
#     return study

# # -----------------------------------------
# # ✅ Model Builders for Evaluation Section
# # -----------------------------------------
# def build_gnb(params):
#     return make_pipeline(StandardScaler(), GaussianNB(var_smoothing=params['var_smoothing']))

# def build_logreg(params):
#     return make_pipeline(StandardScaler(),
#         LogisticRegression(C=params['C'], penalty=params['penalty'], solver='lbfgs', max_iter=1000)
#     )

# def build_svc(params):
#     return make_pipeline(StandardScaler(),
#         SVC(C=params['C'], gamma=params['gamma'], kernel=params['kernel'])
#     )

# def build_rf(params):
#     return RandomForestClassifier(
#         n_estimators=params['n_estimators'],
#         max_depth=params['max_depth'],
#         min_samples_split=params['min_samples_split'],
#         random_state=42
#     )

# def build_xgb(params):
#     return XGBClassifier(
#         n_estimators=params['n_estimators'],
#         max_depth=params['max_depth'],
#         learning_rate=params['learning_rate'],
#         subsample=params['subsample'],
#         colsample_bytree=params['colsample_bytree'],
#         gamma=params['gamma'],
#         use_label_encoder=False,
#         eval_metric='logloss',
#         random_state=42
#     )

# # ----------------------------------------
# # ✅ Evaluation using classification report
# # ----------------------------------------
# def evaluate_on_test(model_builder, best_params, model_name):
#     print(f"\n📊 Classification Report for {model_name}")
#     # X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, test_size=0.2, random_state=42)
#     model = model_builder(best_params)
#     model.fit(X_train, y_train)
#     y_pred = model.predict(X_test)
#     report_dict = classification_report(y_test, y_pred, output_dict=True)
#     print(report_dict)

# # -------------------------
# # ✅ Run for All 5 Models
# # -------------------------
# study = run_study(objective_gnb, "Gaussian Naive Bayes")
# evaluate_on_test(build_gnb, study.best_params, "Gaussian Naive Bayes")

# study = run_study(objective_logreg, "Logistic Regression")
# evaluate_on_test(build_logreg, study.best_params, "Logistic Regression")

# study = run_study(objective_svc, "Support Vector Machine (SVM)")
# evaluate_on_test(build_svc, study.best_params, "Support Vector Machine (SVM)")

# study = run_study(objective_rf, "Random Forest")
# evaluate_on_test(build_rf, study.best_params, "Random Forest")

# study = run_study(objective_xgb, "XGBoost")
# evaluate_on_test(build_xgb, study.best_params, "XGBoost")


In [17]:
# import optuna
# import numpy as np
# import mlflow
# import mlflow.sklearn
# from sklearn.datasets import load_breast_cancer
# from sklearn.model_selection import cross_val_score, StratifiedKFold, train_test_split
# from sklearn.preprocessing import StandardScaler
# from sklearn.pipeline import make_pipeline
# from sklearn.naive_bayes import GaussianNB
# from sklearn.linear_model import LogisticRegression
# from sklearn.svm import SVC
# from sklearn.ensemble import RandomForestClassifier
# from xgboost import XGBClassifier
# from sklearn.metrics import classification_report
# import warnings
# warnings.filterwarnings("ignore")

# # ✅ MLflow experiment setup
# mlflow.set_tracking_uri('http://127.0.0.1:5000')
# mlflow.set_experiment('CodeBasics Beverage survey')

# # ✅ Load dataset
# # X, y = load_breast_cancer(return_X_y=True)
# cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
# # X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, test_size=0.2, random_state=42)

# # ✅ Storage dictionaries for logging
# model_params = {}
# model_metrics = {}
# trained_models = {}

# # ----------------------------
# # ✅ Define Objective Functions
# # ----------------------------
# def objective_gnb(trial):
#     var_smoothing = trial.suggest_float('var_smoothing', 1e-11, 1e-7, log=True)
#     model = make_pipeline(StandardScaler(), GaussianNB(var_smoothing=var_smoothing))
#     return cross_val_score(model, X, y, cv=cv, scoring='accuracy').mean()

# def objective_logreg(trial):
#     c = trial.suggest_float("C", 1e-4, 10.0, log=True)
#     penalty = trial.suggest_categorical("penalty", ["l2"])
#     solver = "lbfgs"
#     model = make_pipeline(StandardScaler(),
#         LogisticRegression(C=c, penalty=penalty, solver=solver, max_iter=1000))
#     return cross_val_score(model, X, y, cv=cv, scoring='accuracy').mean()

# def objective_svc(trial):
#     c = trial.suggest_float("C", 1e-3, 10.0, log=True)
#     gamma = trial.suggest_float("gamma", 1e-4, 1.0, log=True)
#     kernel = trial.suggest_categorical("kernel", ["rbf", "linear"])
#     model = make_pipeline(StandardScaler(),
#         SVC(C=c, gamma=gamma, kernel=kernel))
#     return cross_val_score(model, X, y, cv=cv, scoring='accuracy').mean()

# def objective_rf(trial):
#     n_estimators = trial.suggest_int("n_estimators", 50, 300)
#     max_depth = trial.suggest_int("max_depth", 3, 20)
#     min_samples_split = trial.suggest_int("min_samples_split", 2, 10)
#     model = RandomForestClassifier(
#         n_estimators=n_estimators,
#         max_depth=max_depth,
#         min_samples_split=min_samples_split,
#         random_state=42
#     )
#     return cross_val_score(model, X, y, cv=cv, scoring='accuracy').mean()

# def objective_xgb(trial):
#     param = {
#         'n_estimators': trial.suggest_int('n_estimators', 50, 300),
#         'max_depth': trial.suggest_int('max_depth', 3, 10),
#         'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3, log=True),
#         'subsample': trial.suggest_float('subsample', 0.5, 1.0),
#         'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
#         'gamma': trial.suggest_float('gamma', 0, 5),
#         'use_label_encoder': False,
#         'eval_metric': 'logloss',
#         'random_state': 42
#     }
#     model = XGBClassifier(**param)
#     return cross_val_score(model, X, y, cv=cv, scoring='accuracy').mean()

# # ---------------------------------
# # ✅ Function to Run Optuna Study
# # ---------------------------------
# def run_study(objective_fn, model_name):
#     print(f"\n🔍 Optimizing {model_name}...")
#     study = optuna.create_study(direction='maximize')
#     study.optimize(objective_fn, n_trials=30, timeout=300)
#     print(f"✅ Best Accuracy for {model_name}: {study.best_value:.4f}")
#     print(f"🧠 Best Params: {study.best_params}")
#     return study

# # -----------------------------------------
# # ✅ Model Builders for Evaluation Section
# # -----------------------------------------
# def build_gnb(params):
#     return make_pipeline(StandardScaler(), GaussianNB(var_smoothing=params['var_smoothing']))

# def build_logreg(params):
#     return make_pipeline(StandardScaler(),
#         LogisticRegression(C=params['C'], penalty=params['penalty'], solver='lbfgs', max_iter=1000)
#     )

# def build_svc(params):
#     return make_pipeline(StandardScaler(),
#         SVC(C=params['C'], gamma=params['gamma'], kernel=params['kernel'])
#     )

# def build_rf(params):
#     return RandomForestClassifier(
#         n_estimators=params['n_estimators'],
#         max_depth=params['max_depth'],
#         min_samples_split=params['min_samples_split'],
#         random_state=42
#     )

# def build_xgb(params):
#     return XGBClassifier(
#         n_estimators=params['n_estimators'],
#         max_depth=params['max_depth'],
#         learning_rate=params['learning_rate'],
#         subsample=params['subsample'],
#         colsample_bytree=params['colsample_bytree'],
#         gamma=params['gamma'],
#         use_label_encoder=False,
#         eval_metric='logloss',
#         random_state=42
#     )

# # ----------------------------------------
# # ✅ Evaluation and MLflow logging
# # ----------------------------------------
# def evaluate_on_test(model_builder, best_params, model_name):
#     print(f"\n📊 Classification Report for {model_name}")
#     model = model_builder(best_params)
#     model.fit(X_train, y_train)
#     y_pred = model.predict(X_test)
#     report_dict = classification_report(y_test, y_pred, output_dict=True)
#     print(report_dict)

#     # ⏺ Log everything in global dicts
#     model_params[model_name] = best_params
#     model_metrics[model_name] = report_dict
#     trained_models[model_name] = model

#     # 🎯 Extract metrics for logging
#     metrics_to_log = {
#         "accuracy": report_dict["accuracy"],
#         "precision": report_dict["weighted avg"]["precision"],
#         "recall": report_dict["weighted avg"]["recall"],
#         "f1_score": report_dict["weighted avg"]["f1-score"]
#     }

#     # ✅ Log to MLflow
#     with mlflow.start_run(run_name=model_name):
#         mlflow.log_params(best_params)
#         mlflow.log_metrics(metrics_to_log)
#         mlflow.sklearn.log_model(model, artifact_path=model_name.replace(" ", "_").lower())

#     return best_params, report_dict, model

# # -------------------------
# # ✅ Run for All 5 Models
# # -------------------------
# study = run_study(objective_gnb, "Gaussian Naive Bayes")
# evaluate_on_test(build_gnb, study.best_params, "Gaussian Naive Bayes")

# study = run_study(objective_logreg, "Logistic Regression")
# evaluate_on_test(build_logreg, study.best_params, "Logistic Regression")

# study = run_study(objective_svc, "Support Vector Machine (SVM)")
# evaluate_on_test(build_svc, study.best_params, "Support Vector Machine (SVM)")

# study = run_study(objective_rf, "Random Forest")
# evaluate_on_test(build_rf, study.best_params, "Random Forest")

# study = run_study(objective_xgb, "XGBoost")
# evaluate_on_test(build_xgb, study.best_params, "XGBoost")

# # ✅ Optional: print all results stored
# print("\n📌 Stored Best Parameters:")
# print(model_params)

# print("\n📌 Stored Evaluation Metrics:")
# print(model_metrics)


In [18]:
# import optuna
# import mlflow
# import mlflow.sklearn
# import numpy as np
# from sklearn.datasets import load_breast_cancer
# from sklearn.model_selection import cross_val_score, StratifiedKFold, train_test_split
# from sklearn.preprocessing import StandardScaler
# from sklearn.pipeline import make_pipeline
# from sklearn.naive_bayes import GaussianNB
# from sklearn.linear_model import LogisticRegression
# from sklearn.svm import SVC
# from sklearn.ensemble import RandomForestClassifier
# from xgboost import XGBClassifier
# from sklearn.metrics import classification_report

# # -----------------------
# # ✅ MLflow Configuration
# # -----------------------
# mlflow.set_tracking_uri('http://127.0.0.1:5000')
# mlflow.set_experiment('CodeBasics Beverage survey internship')

# # ----------------------
# # ✅ Load Dataset & Split
# # ----------------------
# # X, y = load_breast_cancer(return_X_y=True)
# # X_train, X_test, y_train, y_test = train_test_split(
# #     X, y, stratify=y, test_size=0.2, random_state=42
# # )
# cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

# # ----------------------------
# # ✅ Define Objective Functions (use X_train only)
# # ----------------------------
# def objective_gnb(trial):
#     var_smoothing = trial.suggest_float('var_smoothing', 1e-11, 1e-7, log=True)
#     model = make_pipeline(StandardScaler(), GaussianNB(var_smoothing=var_smoothing))
#     return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

# def objective_logreg(trial):
#     c = trial.suggest_float("C", 1e-4, 10.0, log=True)
#     penalty = trial.suggest_categorical("penalty", ["l2"])
#     solver = "lbfgs"
#     model = make_pipeline(
#         StandardScaler(),
#         LogisticRegression(C=c, penalty=penalty, solver=solver, max_iter=1000)
#     )
#     return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

# def objective_svc(trial):
#     c = trial.suggest_float("C", 1e-3, 10.0, log=True)
#     gamma = trial.suggest_float("gamma", 1e-4, 1.0, log=True)
#     kernel = trial.suggest_categorical("kernel", ["rbf", "linear"])
#     model = make_pipeline(
#         StandardScaler(),
#         SVC(C=c, gamma=gamma, kernel=kernel)
#     )
#     return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

# def objective_rf(trial):
#     n_estimators = trial.suggest_int("n_estimators", 50, 300)
#     max_depth = trial.suggest_int("max_depth", 3, 20)
#     min_samples_split = trial.suggest_int("min_samples_split", 2, 10)
#     model = RandomForestClassifier(
#         n_estimators=n_estimators,
#         max_depth=max_depth,
#         min_samples_split=min_samples_split,
#         random_state=42
#     )
#     return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

# def objective_xgb(trial):
#     param = {
#         'n_estimators': trial.suggest_int('n_estimators', 50, 300),
#         'max_depth': trial.suggest_int('max_depth', 3, 10),
#         'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3, log=True),
#         'subsample': trial.suggest_float('subsample', 0.5, 1.0),
#         'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
#         'gamma': trial.suggest_float('gamma', 0, 5),
#         'use_label_encoder': False,
#         'eval_metric': 'logloss',
#         'random_state': 42
#     }
#     model = XGBClassifier(**param)
#     return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

# # -------------------------------
# # ✅ Model Builder Functions
# # -------------------------------
# def build_gnb(params):
#     return make_pipeline(StandardScaler(), GaussianNB(var_smoothing=params['var_smoothing']))

# def build_logreg(params):
#     return make_pipeline(
#         StandardScaler(),
#         LogisticRegression(C=params['C'], penalty=params['penalty'], solver='lbfgs', max_iter=1000)
#     )

# def build_svc(params):
#     return make_pipeline(
#         StandardScaler(),
#         SVC(C=params['C'], gamma=params['gamma'], kernel=params['kernel'])
#     )

# def build_rf(params):
#     return RandomForestClassifier(
#         n_estimators=params['n_estimators'],
#         max_depth=params['max_depth'],
#         min_samples_split=params['min_samples_split'],
#         random_state=42
#     )

# def build_xgb(params):
#     return XGBClassifier(
#         n_estimators=params['n_estimators'],
#         max_depth=params['max_depth'],
#         learning_rate=params['learning_rate'],
#         subsample=params['subsample'],
#         colsample_bytree=params['colsample_bytree'],
#         gamma=params['gamma'],
#         use_label_encoder=False,
#         eval_metric='logloss',
#         random_state=42
#     )

# # ----------------------------------------
# # ✅ Evaluate on Test + Log with MLflow
# # ----------------------------------------
# def evaluate_on_test(model_builder, best_params, model_name):
#     print(f"\n📊 Classification Report for {model_name}")
#     model = model_builder(best_params)
#     model.fit(X_train, y_train)
#     y_pred = model.predict(X_test)

#     report_dict = classification_report(y_test, y_pred, output_dict=True)

#     metrics_to_log = {
#         "accuracy": report_dict["accuracy"],
#         "precision": report_dict["weighted avg"]["precision"],
#         "recall": report_dict["weighted avg"]["recall"],
#         "f1_score": report_dict["weighted avg"]["f1-score"]
#     }

#     print(metrics_to_log)

#     with mlflow.start_run(run_name=model_name):
#         mlflow.log_params(best_params)
#         mlflow.log_metrics(metrics_to_log)
#         mlflow.sklearn.log_model(model, artifact_path=model_name.replace(" ", "_").lower())

#     return best_params, metrics_to_log

# # --------------------------------
# # ✅ Study Runner Function
# # --------------------------------
# def run_study_and_log(objective_fn, model_builder, model_name):
#     print(f"\n🔍 Optimizing {model_name}...")
#     study = optuna.create_study(direction='maximize')
#     study.optimize(objective_fn, n_trials=30, timeout=300)

#     print(f"✅ Best Accuracy for {model_name}: {study.best_value:.4f}")
#     print(f"🧠 Best Params: {study.best_params}")

#     best_params, metrics = evaluate_on_test(model_builder, study.best_params, model_name)
#     return best_params, metrics

# # --------------------------
# # ✅ Run All Models
# # --------------------------
# results = {}

# results["Gaussian Naive Bayes"] = run_study_and_log(objective_gnb, build_gnb, "Gaussian Naive Bayes")
# results["Logistic Regression"] = run_study_and_log(objective_logreg, build_logreg, "Logistic Regression")
# results["Support Vector Machine (SVM)"] = run_study_and_log(objective_svc, build_svc, "Support Vector Machine (SVM)")
# results["Random Forest"] = run_study_and_log(objective_rf, build_rf, "Random Forest")
# results["XGBoost"] = run_study_and_log(objective_xgb, build_xgb, "XGBoost")

# # Optional: print(results["XGBoost"]) to access params and metrics


In [19]:
# import optuna
# import mlflow
# import mlflow.sklearn
# import numpy as np
# from sklearn.datasets import load_breast_cancer
# from sklearn.model_selection import cross_val_score, StratifiedKFold, train_test_split
# from sklearn.preprocessing import StandardScaler
# from sklearn.pipeline import make_pipeline
# from sklearn.naive_bayes import GaussianNB
# from sklearn.linear_model import LogisticRegression
# from sklearn.svm import SVC
# from sklearn.ensemble import RandomForestClassifier
# from xgboost import XGBClassifier
# from lightgbm import LGBMClassifier
# from sklearn.metrics import classification_report

# # -----------------------
# # ✅ MLflow Configuration
# # -----------------------
# mlflow.set_tracking_uri('http://127.0.0.1:5000')
# mlflow.set_experiment('Beverage Price Prediction')

# # ----------------------
# # ✅ Load Dataset & Split
# # ----------------------
# # X, y = load_breast_cancer(return_X_y=True)
# # X_train, X_test, y_train, y_test = train_test_split(
# #     X, y, stratify=y, test_size=0.2, random_state=42
# # )
# cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

# # ----------------------------
# # ✅ Define Objective Functions
# # ----------------------------
# def objective_gnb(trial):
#     var_smoothing = trial.suggest_float('var_smoothing', 1e-11, 1e-7, log=True)
#     model = make_pipeline(StandardScaler(), GaussianNB(var_smoothing=var_smoothing))
#     return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

# def objective_logreg(trial):
#     c = trial.suggest_float("C", 1e-4, 10.0, log=True)
#     penalty = trial.suggest_categorical("penalty", ["l2"])
#     solver = "lbfgs"
#     model = make_pipeline(
#         StandardScaler(),
#         LogisticRegression(C=c, penalty=penalty, solver=solver, max_iter=1000)
#     )
#     return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

# def objective_svc(trial):
#     c = trial.suggest_float("C", 1e-3, 10.0, log=True)
#     gamma = trial.suggest_float("gamma", 1e-4, 1.0, log=True)
#     kernel = trial.suggest_categorical("kernel", ["rbf", "linear"])
#     model = make_pipeline(
#         StandardScaler(),
#         SVC(C=c, gamma=gamma, kernel=kernel)
#     )
#     return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

# def objective_rf(trial):
#     n_estimators = trial.suggest_int("n_estimators", 50, 300)
#     max_depth = trial.suggest_int("max_depth", 3, 20)
#     min_samples_split = trial.suggest_int("min_samples_split", 2, 10)
#     model = RandomForestClassifier(
#         n_estimators=n_estimators,
#         max_depth=max_depth,
#         min_samples_split=min_samples_split,
#         random_state=42
#     )
#     return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

# def objective_xgb(trial):
#     param = {
#         'n_estimators': trial.suggest_int('n_estimators', 50, 300),
#         'max_depth': trial.suggest_int('max_depth', 3, 10),
#         'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3, log=True),
#         'subsample': trial.suggest_float('subsample', 0.5, 1.0),
#         'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
#         'gamma': trial.suggest_float('gamma', 0, 5),
#         'use_label_encoder': False,
#         'eval_metric': 'logloss',
#         'random_state': 42
#     }
#     model = XGBClassifier(**param)
#     return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

# def objective_lgb(trial):
#     param = {
#         'n_estimators': trial.suggest_int('n_estimators', 50, 300),
#         'max_depth': trial.suggest_int('max_depth', 3, 10),
#         'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3, log=True),
#         'subsample': trial.suggest_float('subsample', 0.5, 1.0),
#         'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
#         'random_state': 42
#     }
#     model = LGBMClassifier(**param)
#     return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

# # -------------------------------
# # ✅ Model Builder Functions
# # -------------------------------
# def build_gnb(params):
#     return make_pipeline(StandardScaler(), GaussianNB(var_smoothing=params['var_smoothing']))

# def build_logreg(params):
#     return make_pipeline(
#         StandardScaler(),
#         LogisticRegression(C=params['C'], penalty=params['penalty'], solver='lbfgs', max_iter=1000)
#     )

# def build_svc(params):
#     return make_pipeline(
#         StandardScaler(),
#         SVC(C=params['C'], gamma=params['gamma'], kernel=params['kernel'])
#     )

# def build_rf(params):
#     return RandomForestClassifier(
#         n_estimators=params['n_estimators'],
#         max_depth=params['max_depth'],
#         min_samples_split=params['min_samples_split'],
#         random_state=42
#     )

# def build_xgb(params):
#     return XGBClassifier(
#         n_estimators=params['n_estimators'],
#         max_depth=params['max_depth'],
#         learning_rate=params['learning_rate'],
#         subsample=params['subsample'],
#         colsample_bytree=params['colsample_bytree'],
#         gamma=params['gamma'],
#         use_label_encoder=False,
#         eval_metric='logloss',
#         random_state=42
#     )

# def build_lgb(params):
#     return LGBMClassifier(
#         n_estimators=params['n_estimators'],
#         max_depth=params['max_depth'],
#         learning_rate=params['learning_rate'],
#         subsample=params['subsample'],
#         colsample_bytree=params['colsample_bytree'],
#         random_state=42
#     )

# # ----------------------------------------
# # ✅ Evaluate on Test + Log with MLflow
# # ----------------------------------------
# def evaluate_on_test(model_builder, best_params, model_name):
#     print(f"\n📊 Classification Report for {model_name}")
#     model = model_builder(best_params)
#     model.fit(X_train, y_train)
#     y_pred = model.predict(X_test)

#     report_dict = classification_report(y_test, y_pred, output_dict=True)

#     metrics_to_log = {
#         "accuracy": report_dict["accuracy"],
#         "precision": report_dict["weighted avg"]["precision"],
#         "recall": report_dict["weighted avg"]["recall"],
#         "f1_score": report_dict["weighted avg"]["f1-score"]
#     }

#     print(metrics_to_log)

#     with mlflow.start_run(run_name=model_name):
#         mlflow.log_params(best_params)
#         mlflow.log_metrics(metrics_to_log)
#         mlflow.sklearn.log_model(model, artifact_path=model_name.replace(" ", "_").lower())

#     return best_params, metrics_to_log

# # --------------------------------
# # ✅ Study Runner Function
# # --------------------------------
# def run_study_and_log(objective_fn, model_builder, model_name):
#     print(f"\n🔍 Optimizing {model_name}...")
#     study = optuna.create_study(direction='maximize')
#     study.optimize(objective_fn, n_trials=30, timeout=300)

#     print(f"✅ Best Accuracy for {model_name}: {study.best_value:.4f}")
#     print(f"🧠 Best Params: {study.best_params}")

#     best_params, metrics = evaluate_on_test(model_builder, study.best_params, model_name)
#     return best_params, metrics

# # --------------------------
# # ✅ Run All Models
# # --------------------------
# results = {}
# results["Gaussian Naive Bayes"] = run_study_and_log(objective_gnb, build_gnb, "Gaussian Naive Bayes")
# results["Logistic Regression"] = run_study_and_log(objective_logreg, build_logreg, "Logistic Regression")
# results["Support Vector Machine (SVM)"] = run_study_and_log(objective_svc, build_svc, "Support Vector Machine (SVM)")
# results["Random Forest"] = run_study_and_log(objective_rf, build_rf, "Random Forest")
# results["XGBoost"] = run_study_and_log(objective_xgb, build_xgb, "XGBoost")
# results["LightGBM"] = run_study_and_log(objective_lgb, build_lgb, "LightGBM")

# # Optional: print(results["LightGBM"])


In [20]:
import optuna
import mlflow
import mlflow.sklearn
import numpy as np
from sklearn.model_selection import cross_val_score, StratifiedKFold, train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import make_pipeline
from sklearn.naive_bayes import GaussianNB
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from sklearn.metrics import classification_report

# -----------------------
# ✅ MLflow Configuration
# -----------------------
mlflow.set_tracking_uri('http://127.0.0.1:5000')
mlflow.set_experiment('Beverage Price Prediction')

cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

# ----------------------------
# ✅ Define Objective Functions
# ----------------------------
def objective_gnb(trial):
    var_smoothing = trial.suggest_float('var_smoothing', 1e-11, 1e-7, log=True)
    model = make_pipeline(StandardScaler(), GaussianNB(var_smoothing=var_smoothing))
    return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

def objective_logreg(trial):
    c = trial.suggest_float("C", 1e-4, 10.0, log=True)
    penalty = trial.suggest_categorical("penalty", ["l2"])
    solver = "lbfgs"
    model = make_pipeline(
        StandardScaler(),
        LogisticRegression(C=c, penalty=penalty, solver=solver, max_iter=1000)
    )
    return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

def objective_svc(trial):
    c = trial.suggest_float("C", 1e-3, 10.0, log=True)
    gamma = trial.suggest_float("gamma", 1e-4, 1.0, log=True)
    kernel = trial.suggest_categorical("kernel", ["rbf", "linear"])
    model = make_pipeline(
        StandardScaler(),
        SVC(C=c, gamma=gamma, kernel=kernel)
    )
    return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

def objective_rf(trial):
    n_estimators = trial.suggest_int("n_estimators", 50, 300)
    max_depth = trial.suggest_int("max_depth", 3, 20)
    min_samples_split = trial.suggest_int("min_samples_split", 2, 10)
    model = RandomForestClassifier(
        n_estimators=n_estimators,
        max_depth=max_depth,
        min_samples_split=min_samples_split,
        random_state=42
    )
    return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

def objective_xgb(trial):
    param = {
        'n_estimators': trial.suggest_int('n_estimators', 50, 300),
        'max_depth': trial.suggest_int('max_depth', 3, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3, log=True),
        'subsample': trial.suggest_float('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
        'gamma': trial.suggest_float('gamma', 0, 5),
        'use_label_encoder': False,
        'eval_metric': 'logloss',
        'random_state': 42
    }
    model = XGBClassifier(**param)
    return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

def objective_lgb(trial):
    param = {
        'n_estimators': trial.suggest_int('n_estimators', 50, 300),
        'max_depth': trial.suggest_int('max_depth', 3, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3, log=True),
        'subsample': trial.suggest_float('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
        'random_state': 42
    }
    model = LGBMClassifier(**param)
    return cross_val_score(model, X_train, y_train, cv=cv, scoring='accuracy').mean()

# -------------------------------
# ✅ Model Builder Functions
# -------------------------------
def build_gnb(params):
    return make_pipeline(StandardScaler(), GaussianNB(var_smoothing=params['var_smoothing']))

def build_logreg(params):
    return make_pipeline(
        StandardScaler(),
        LogisticRegression(C=params['C'], penalty=params['penalty'], solver='lbfgs', max_iter=1000)
    )

def build_svc(params):
    return make_pipeline(
        StandardScaler(),
        SVC(C=params['C'], gamma=params['gamma'], kernel=params['kernel'])
    )

def build_rf(params):
    return RandomForestClassifier(
        n_estimators=params['n_estimators'],
        max_depth=params['max_depth'],
        min_samples_split=params['min_samples_split'],
        random_state=42
    )

def build_xgb(params):
    return XGBClassifier(
        n_estimators=params['n_estimators'],
        max_depth=params['max_depth'],
        learning_rate=params['learning_rate'],
        subsample=params['subsample'],
        colsample_bytree=params['colsample_bytree'],
        gamma=params['gamma'],
        use_label_encoder=False,
        eval_metric='logloss',
        random_state=42
    )

def build_lgb(params):
    return LGBMClassifier(
        n_estimators=params['n_estimators'],
        max_depth=params['max_depth'],
        learning_rate=params['learning_rate'],
        subsample=params['subsample'],
        colsample_bytree=params['colsample_bytree'],
        random_state=42
    )

# ----------------------------------------
# ✅ Evaluate on Test + Log & Register Model with MLflow
# ----------------------------------------
def evaluate_on_test(model_builder, best_params, model_name):
    print(f"\n📊 Classification Report for {model_name}")
    model = model_builder(best_params)
    model.fit(X_train, y_train)
    y_pred = model.predict(X_test)

    report_dict = classification_report(y_test, y_pred, output_dict=True)

    metrics_to_log = {
        "accuracy": report_dict["accuracy"],
        "precision": report_dict["weighted avg"]["precision"],
        "recall": report_dict["weighted avg"]["recall"],
        "f1_score": report_dict["weighted avg"]["f1-score"]
    }

    print(metrics_to_log)

    with mlflow.start_run(run_name=model_name):
        mlflow.log_params(best_params)
        mlflow.log_metrics(metrics_to_log)
        mlflow.sklearn.log_model(
            sk_model=model,
            artifact_path=model_name.replace(" ", "_").lower(),
            registered_model_name=model_name.replace(" ", "_")  # Register model
        )

    return best_params, metrics_to_log

# --------------------------------
# ✅ Study Runner Function
# --------------------------------
def run_study_and_log(objective_fn, model_builder, model_name):
    print(f"\n🔍 Optimizing {model_name}...")
    study = optuna.create_study(direction='maximize')
    study.optimize(objective_fn, n_trials=30, timeout=300)

    print(f"✅ Best Accuracy for {model_name}: {study.best_value:.4f}")
    print(f"🧠 Best Params: {study.best_params}")

    best_params, metrics = evaluate_on_test(model_builder, study.best_params, model_name)
    return best_params, metrics

# --------------------------
# ✅ Run All Models
# --------------------------
results = {}
results["Gaussian Naive Bayes"] = run_study_and_log(objective_gnb, build_gnb, "Gaussian Naive Bayes")
results["Logistic Regression"] = run_study_and_log(objective_logreg, build_logreg, "Logistic Regression")
results["Support Vector Machine (SVM)"] = run_study_and_log(objective_svc, build_svc, "Support Vector Machine (SVM)")
results["Random Forest"] = run_study_and_log(objective_rf, build_rf, "Random Forest")
results["XGBoost"] = run_study_and_log(objective_xgb, build_xgb, "XGBoost")
results["LightGBM"] = run_study_and_log(objective_lgb, build_lgb, "LightGBM")

# Optional: print(results["LightGBM"])


2025/07/23 13:23:27 INFO mlflow.tracking.fluent: Experiment with name 'Beverage Price Prediction' does not exist. Creating a new experiment.
[I 2025-07-23 13:23:27,993] A new study created in memory with name: no-name-0ba07b51-92f2-4ae4-9f04-d02826cea24d



🔍 Optimizing Gaussian Naive Bayes...


[I 2025-07-23 13:23:28,281] Trial 0 finished with value: 0.5682558370232447 and parameters: {'var_smoothing': 5.443422592331397e-10}. Best is trial 0 with value: 0.5682558370232447.
[I 2025-07-23 13:23:28,571] Trial 1 finished with value: 0.5761341654837455 and parameters: {'var_smoothing': 2.74816723148772e-08}. Best is trial 1 with value: 0.5761341654837455.
[I 2025-07-23 13:23:28,839] Trial 2 finished with value: 0.5734634729729903 and parameters: {'var_smoothing': 1.2493129430657581e-08}. Best is trial 1 with value: 0.5761341654837455.
[I 2025-07-23 13:23:29,123] Trial 3 finished with value: 0.5649620123118878 and parameters: {'var_smoothing': 6.398089143384444e-11}. Best is trial 1 with value: 0.5761341654837455.
[I 2025-07-23 13:23:29,357] Trial 4 finished with value: 0.5705258072909933 and parameters: {'var_smoothing': 3.2522202013283696e-09}. Best is trial 1 with value: 0.5761341654837455.
[I 2025-07-23 13:23:29,659] Trial 5 finished with value: 0.5734634729729903 and parameter

✅ Best Accuracy for Gaussian Naive Bayes: 0.5794
🧠 Best Params: {'var_smoothing': 9.978096996076583e-08}

📊 Classification Report for Gaussian Naive Bayes
{'accuracy': 0.5807183869675524, 'precision': 0.5802790431347046, 'recall': 0.5807183869675524, 'f1_score': 0.5524848403381709}


2025/07/23 13:23:55 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
Successfully registered model 'Gaussian_Naive_Bayes'.
2025/07/23 13:23:56 INFO mlflow.store.model_registry.abstract_store: Waiting up to 300 seconds for model version to finish creation. Model name: Gaussian_Naive_Bayes, version 1
Created version '1' of model 'Gaussian_Naive_Bayes'.
[I 2025-07-23 13:23:56,554] A new study created in memory with name: no-name-7619313a-f7ab-4bb5-98d7-aa15ad4529f7


...

[I 2025-07-23 13:46:23,244] Trial 29 finished with value: 0.9193929715719582 and parameters: {'n_estimators': 140, 'max_depth': 5, 'learning_rate': 0.16535234662207812, 'subsample': 0.7336102246211148, 'colsample_bytree': 0.9988161282030531}. Best is trial 23 with value: 0.9249121240963172.


✅ Best Accuracy for LightGBM: 0.9249
🧠 Best Params: {'n_estimators': 271, 'max_depth': 4, 'learning_rate': 0.2285707313051734, 'subsample': 0.7236565637589563, 'colsample_bytree': 0.9140352418184015}

📊 Classification Report for LightGBM
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000831 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 136
[LightGBM] [Info] Number of data points in the train set: 22467, number of used features: 28
[LightGBM] [Info] Start training from score -1.343386
[LightGBM] [Info] Start training from score -1.228925
[LightGBM] [Info] Start training from score -1.126779
[LightGBM] [Info] Start training from score -2.100810
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits 

2025/07/23 13:46:31 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
Successfully registered model 'LightGBM'.
2025/07/23 13:46:31 INFO mlflow.store.model_registry.abstract_store: Waiting up to 300 seconds for model version to finish creation. Model name: LightGBM, version 1


🏃 View run LightGBM at: http://127.0.0.1:5000/#/experiments/104226191654138827/runs/e83c5287fcc24f87a947ae0b6228c5d4
🧪 View experiment at: http://127.0.0.1:5000/#/experiments/104226191654138827


Created version '1' of model 'LightGBM'.
